In [1]:
import pandas as pd
import numpy as np
from math import sqrt

In [2]:
# ic 計算
def daily_ic(group):
    return group['factor'].corr(group['ret_fwd_1d'], method='spearman')

In [3]:
# 向量化計算 daily spearman ic
def daily_spearman_ic_vectorized(df, factor_col, ret_col='ret_fwd_1d'):
    tmp = df[['date', 'ticker', factor_col, ret_col]].dropna().copy()
    g = tmp['date']

    # Spearman = corr(rank(x), rank(y))
    x = tmp.groupby('date')[factor_col].rank(method='average')
    y = tmp.groupby('date')[ret_col].rank(method='average')

    dx = x - x.groupby(g).transform('mean')
    dy = y - y.groupby(g).transform('mean')

    num = (dx * dy).groupby(g).sum()
    den = np.sqrt((dx * dx).groupby(g).sum() * (dy * dy).groupby(g).sum())

    ic_ts = num / den
    ic_ts.name = factor_col
    return ic_ts

In [4]:
def preprocess_factors(df, factor_cols):

    df = df.copy()
    
    # 缺失值填補 (Imputation) - 全市場中位數
    print("Step 1: 正在進行缺失值填補 (全市場中位數)...")
    
    def fill_median(x):
        return x.fillna(x.median())

    # 針對每一天 (level='Date')，對指定的因子欄位進行中位數填補
    for col in factor_cols:
        df[col] = df.groupby(level='date')[col].transform(fill_median).fillna(0)

    # 去極值 (Winsorization) - 使用百分位法 (1% ~ 99%)
    print("正在進行去極值 (Winsorization 1% - 99%)...")
    
    def clip_outliers(x):
        # 計算當天的 1% 和 99% 分位點
        lower = x.quantile(0.01)
        upper = x.quantile(0.99)
        return x.clip(lower, upper)

    for col in factor_cols:
        df[col] = df.groupby(level='date')[col].transform(clip_outliers)
    return df

def preprocess_factors_zcore(df, factor_cols):
    df = df.copy()
    print("正在進行標準化 (Z-score)...")
    def z_score(x):
        # 避免標準差為 0 的情況 (例如當天所有股票數值都一樣)
        std = x.std()
        if std == 0:
            return 0
        return (x - x.mean()) / std

    for col in factor_cols:
        df[col] = df.groupby(level='date')[col].transform(z_score)

    return df

In [5]:
factors_data = pd.read_pickle('data/factors_data_log60.pkl')

In [6]:
N_DAYS = 5

factors_data['ret_future'] = factors_data.groupby('ticker')['close'].transform(
    lambda x: x.shift(-N_DAYS) / x - 1
)

factors_data['label'] = factors_data.groupby('date')['ret_future'].transform(
    lambda x: x.rank(pct=True)
)

factors_data['label'] = factors_data['label'] - 0.5
factors_data = factors_data.loc[:, ~factors_data.columns.duplicated()].copy()

# date 欄位保證存在且為 datetime
if 'date' not in factors_data.columns:
    factors_data = factors_data.sort_index()
    factors_data['date'] = factors_data.index
factors_data['date'] = pd.to_datetime(factors_data['date']).dt.normalize()

base_cols = {
    'date','ticker','open','high','low','close','volume','returns',
    'ret_fwd_1d',   
}

factor_cols = [c for c in factors_data.columns if c not in base_cols]
factor_cols.sort()

/var/folders/gk/tqz928vx1m96n53nylzj1y800000gn/T/ipykernel_19337/474235013.py:3: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  factors_data['ret_future'] = factors_data.groupby('ticker')['close'].transform(
/var/folders/gk/tqz928vx1m96n53nylzj1y800000gn/T/ipykernel_19337/474235013.py:7: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  factors_data['label'] = factors_data.groupby('date')['ret_future'].transform(


In [8]:
results = {}
summary_rows = []

for col in factor_cols:
    ic_ts = daily_spearman_ic_vectorized(factors_data, col, ret_col='ret_future')
    results[col] = ic_ts

    vals = ic_ts.to_numpy(dtype='float64')
    vals = vals[~np.isnan(vals)]

    if vals.size == 0:
        ic_mean = ic_std = ic_ir = pct_pos = np.nan
        n_days = 0
    else:
        ic_mean = vals.mean()
        ic_std  = vals.std(ddof=1) if vals.size > 1 else np.nan
        ic_ir   = ic_mean / ic_std if (ic_std is not None and ic_std > 0) else np.nan
        pct_pos = (vals > 0).mean()
        n_days  = vals.size

    summary_rows.append({
        'factor': col,
        'ic_mean': ic_mean,
        'ic_std': ic_std,
        'ic_ir': ic_ir,
        'pct_positive': pct_pos,
        'n_days': n_days,
    })

ic_summary = pd.DataFrame(summary_rows).sort_values('ic_ir', ascending=False)
ic_summary.to_csv('ic_summary_rank.csv', index=False)

In [9]:
ic_summary = pd.read_csv('ic_summary_rank.csv')
ic_summary.head(20)

factor   ic_mean    ic_std     ic_ir  \
0                                price3  0.061240  0.089407  0.684958   
1                                  min5  0.068287  0.104851  0.651276   
2                             alpha_013  0.042363  0.069527  0.609307   
3                             alpha_016  0.043416  0.076637  0.566514   
4                                 min10  0.059609  0.108867  0.547544   
5                           ep_ttm_rank  0.049981  0.092242  0.541843   
6                                ep_ttm  0.049981  0.092242  0.541843   
7                             alpha_055  0.034616  0.064501  0.536673   
8                                 qtld5  0.055076  0.104336  0.527869   
9                             alpha_015  0.032631  0.062939  0.518457   
10                            alpha_088  0.059824  0.115985  0.515791   
11                            alpha_044  0.033739  0.070618  0.477772   
12                               qtld10  0.050707  0.106384  0.476641   
13                            alpha_035  0.033213  0.071616  0.463758   
14                            alpha_002  0.021977  0.049316  0.445637   
15                            alpha_040  0.048426  0.109725  0.441336   
16                            alpha_012  0.026783  0.062883  0.425923   
17                                min20  0.048197  0.113616  0.424210   
18                            alpha_043  0.026085  0.063148  0.413067   
19  TotalConsolidatedProfitForThePeriod  0.037098  0.092326  0.401818   

    pct_positive  n_days  
0       0.790803    2653  
1       0.754994    2653  
2       0.731523    2652  
3       0.720588    2652  
4       0.710139    2653  
5       0.742857    2555  
6       0.742857    2555  
7       0.719728    2651  
8       0.724359    2652  
9       0.692308    2652  
10      0.716190    2625  
11      0.690799    2652  
12      0.700603    2652  
13      0.692484    2621  
14      0.678747    2649  
15      0.665534    2649  
16      0.703284    2649  
17      0.665662    2653  
18      0.680714    2634  
19      0.677091    2558

In [26]:
factor_cols.remove('effective_date')
factor_cols.remove('report_date')

ValueError: list.remove(x): x not in list

In [12]:
df = factors_data.drop(columns=['open', 'high', 'low', 'volume', 'returns', 'ret_fwd_1d','effective_date','report_date'])
df1 = df.set_index(['date', 'ticker'])

In [ ]:
#(13m48s)
processed_df = preprocess_factors(df1, factor_cols)

Step 1: 正在進行缺失值填補 (全市場中位數)...


/Users/you-kaihsu/Desktop/Project/.conda/lib/python3.11/site-packages/numpy/lib/_nanfunctions_impl.py:1214: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/Users/you-kaihsu/Desktop/Project/.conda/lib/python3.11/site-packages/numpy/lib/_nanfunctions_impl.py:1214: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/Users/you-kaihsu/Desktop/Project/.conda/lib/python3.11/site-packages/numpy/lib/_nanfunctions_impl.py:1214: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/Users/you-kaihsu/Desktop/Project/.conda/lib/python3.11/site-packages/numpy/lib/_nanfunctions_impl.py:1214: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/Users/you-kaihsu/Desktop/Project/.conda/lib/python3.11/site-packages/numpy/lib/_nanfunctions_impl.py:1214: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepd

正在進行去極值 (Winsorization 1% - 99%)...


In [14]:
processed_df.to_pickle("data/processed_df.pkl")

In [8]:
processed_df1 = pd.read_pickle("data/processed_df.pkl")

In [9]:
processed_df1

close  AccountsPayable_x  AccountsPayable_per  \
date       ticker                                                       
2015-06-01 1101.TW  18.344522       6.927581e+09                 2.39   
2015-06-02 1101.TW  18.032085       6.927581e+09                 2.39   
2015-06-03 1101.TW  17.920500       6.927581e+09                 2.39   
2015-06-04 1101.TW  17.317945       6.927581e+09                 2.39   
2015-06-05 1101.TW  17.384897       6.927581e+09                 2.39   
...                       ...                ...                  ...   
2015-05-25 9958.TW   7.179392       0.000000e+00                 0.00   
2015-05-26 9958.TW   7.123982       0.000000e+00                 0.00   
2015-05-27 9958.TW   7.084403       0.000000e+00                 0.00   
2015-05-28 9958.TW   7.195221       0.000000e+00                 0.00   
2015-05-29 9958.TW   7.123982       0.000000e+00                 0.00   

                    AccountsReceivableNet  AccountsReceivableNet_per  \
date       ticker                                                      
2015-06-01 1101.TW           7.211579e+09                       2.49   
2015-06-02 1101.TW           7.211579e+09                       2.49   
2015-06-03 1101.TW           7.211579e+09                       2.49   
2015-06-04 1101.TW           7.211579e+09                       2.49   
2015-06-05 1101.TW           7.211579e+09                       2.49   
...                                   ...                        ...   
2015-05-25 9958.TW           0.000000e+00                       0.00   
2015-05-26 9958.TW           0.000000e+00                       0.00   
2015-05-27 9958.TW           0.000000e+00                       0.00   
2015-05-28 9958.TW           0.000000e+00                       0.00   
2015-05-29 9958.TW           0.000000e+00                       0.00   

                    CapitalSurplus  CapitalSurplus_per  \
date       ticker                                        
2015-06-01 1101.TW    1.222523e+10                4.22   
2015-06-02 1101.TW    1.222523e+10                4.22   
2015-06-03 1101.TW    1.222523e+10                4.22   
2015-06-04 1101.TW    1.222523e+10                4.22   
2015-06-05 1101.TW    1.222523e+10                4.22   
...                            ...                 ...   
2015-05-25 9958.TW    0.000000e+00                0.00   
2015-05-26 9958.TW    0.000000e+00                0.00   
2015-05-27 9958.TW    0.000000e+00                0.00   
2015-05-28 9958.TW    0.000000e+00                0.00   
2015-05-29 9958.TW    0.000000e+00                0.00   

                    CashAndCashEquivalents  CashAndCashEquivalents_per  \
date       ticker                                                        
2015-06-01 1101.TW            3.140622e+10                       10.84   
2015-06-02 1101.TW            3.140622e+10                       10.84   
2015-06-03 1101.TW            3.140622e+10                       10.84   
2015-06-04 1101.TW            3.140622e+10                       10.84   
2015-06-05 1101.TW            3.140622e+10                       10.84   
...                                    ...                         ...   
2015-05-25 9958.TW            0.000000e+00                        0.00   
2015-05-26 9958.TW            0.000000e+00                        0.00   
2015-05-27 9958.TW            0.000000e+00                        0.00   
2015-05-28 9958.TW            0.000000e+00                        0.00   
2015-05-29 9958.TW            0.000000e+00                        0.00   

                    CurrentAssets  ...  pretax_margin  cfo_margin  accruals  \
date       ticker                  ...                                        
2015-06-01 1101.TW   9.247110e+10  ...       0.068557    0.298419 -0.018716   
2015-06-02 1101.TW   9.247110e+10  ...       0.068557    0.298419 -0.018716   
2015-06-03 1101.TW   9.247110e+10  ...       0.068557    0.298419 -0.018716   
2015-06-04 1101.TW   9.2

In [27]:
# 標準化 （ram 不夠用 只能分開寫）
processed_df2 = preprocess_factors_zcore(processed_df1, factor_cols)

正在進行標準化 (Z-score)...


In [29]:
processed_df3 = processed_df2.fillna(0)
processed_df3.isna().sum()

close                        0
AccountsPayable_x            0
AccountsPayable_per          0
AccountsReceivableNet        0
AccountsReceivableNet_per    0
                            ..
de_ratio                     0
current_ratio                0
quick_ratio                  0
cash_ratio                   0
label                        0
Length: 345, dtype: int64

In [30]:
df_long = processed_df3.reset_index()

In [31]:
df_long.sort_values(['ticker', 'date']).reset_index(drop=True).to_pickle('data/processed_factors_data_log60.pkl')

: 

In [14]:
df_long.sort_values(['ticker', 'date']).reset_index(drop=True).to_csv('data/processed_factors_data_log60.csv', index=False)